# Summary of AGIPD dark characterization #

The following report shows a set of dark images taken with the AGIPD detector to deduce detector offsets, noise, bad-pixel maps and thresholding. All four types of constants are evaluated per-pixel and per-memory cell.


**The offset** ($O$) is defined as the median ($M$) of the dark signal ($Ds$) over trains ($t$) for a given pixel ($x,y$) and memory cell ($c$). 

**The noise** $N$ is the standard deviation $\sigma$ of the dark signal.

$$ O_{x,y,c} = M(Ds)_{t} ,\,\,\,\,\,\, N_{x,y,c} = \sigma(Ds)_{t}$$

**The bad pixel** mask is encoded as a bit mask.

**"OFFSET_OUT_OF_THRESHOLD":**

Offset outside of bounds:

$$M(O)_{x,y} - \sigma(O)_{x,y} * \mathrm{thresholds\_offset\_sigma} < O < M(O)_{x,y} + \sigma(O)_{x,y} * \mathrm{thresholds\_offset\_sigma} $$

or offset outside of hard limits

$$ \mathrm{thresholds\_offset\_hard}_\mathrm{low} < O < \mathrm{thresholds\_offset\_hard}_\mathrm{high} $$

**"NOISE_OUT_OF_THRESHOLD":**

Noise outside of bounds:

$$M(N)_{x,y} - \sigma(N)_{x,y} * \mathrm{thresholds\_noise\_sigma} < N < M(N)_{x,y} + \sigma(N)_{x,y} * \mathrm{thresholds\_noise\_sigma} $$

or noise outside of hard limits

$$\mathrm{thresholds\_noise\_hard}_\mathrm{low} < N < \mathrm{thresholds\_noise\_hard}_\mathrm{high} $$

**"OFFSET_NOISE_EVAL_ERROR":**

Offset and Noise both not $nan$ values 

Values: $\mathrm{thresholds\_offset\_sigma}$, $\mathrm{thresholds\_offset\_hard}$, $\mathrm{thresholds\_noise\_sigma}$, $\mathrm{thresholds\_noise\_hard}$ are given as parameters.

In [ ]:
cluster_profile = "noDB" # The ipcluster profile to use
out_folder = "/gpfs/exfel/data/scratch/ahmedk/test/SPB/DARK/AGIPD1/" # path to output to, required
dinstance = "AGIPD1M1" # detector instance
gain_names = ['High gain', 'Medium gain', 'Low gain'] # a list of gain names to be used in plotting
threshold_names = ['HG-MG threshold', 'MG_LG threshold'] # a list of gain names to be used in plotting

In [ ]:
from collections import OrderedDict
import copy
from datetime import datetime
import os
import warnings
warnings.filterwarnings('ignore')

import glob
import h5py
from IPython.display import display, Markdown, Latex
import numpy as np
import matplotlib
matplotlib.use("agg")
import matplotlib.gridspec as gridspec
import matplotlib.patches as patches
import matplotlib.pyplot as plt
%matplotlib inline
import tabulate
from cal_tools.ana_tools import get_range
from extra_geom import AGIPD_1MGeometry
from iCalibrationDB import Detectors
from XFELDetAna.plotting.heatmap import heatmapPlot
from XFELDetAna.plotting.simpleplot import simplePlot

In [ ]:
# TODO: After changes in the Cal DB interface read files from cal repository

# Load constants from local files
data = OrderedDict()
old_cons = OrderedDict()
mod_names = []
# Loop over modules
for i in range(16):
    qm = "Q{}M{}".format(i//4 + 1, i % 4 + 1)
    # loop over constants
    detinst = getattr(Detectors, dinstance)
    for const in ['Offset', 'Noise', 'ThresholdsDark', 'BadPixelsDark']:
        det = getattr(detinst, qm)
        if det is None:
            continue
        det_name = det.device_name

        fpath = '{}/const_{}_{}.h5'.format(out_folder, const, det_name)
        oldfpath = '{}/old/const_{}_{}.h5'.format(out_folder, const, det_name)
        if not os.path.isfile(fpath):
            continue
        with h5py.File(fpath, 'r') as f:
            if qm not in data:
                mod_names.append(qm)
                data[qm] = OrderedDict()

            data[qm][const] = f["data"][()]

        if not os.path.isfile(oldfpath):
            continue

        with h5py.File(oldfpath, 'r') as oldf:
            if qm not in old_cons:
                old_cons[qm] = OrderedDict()
            old_cons[qm][const] = oldf["data"][()]


In [ ]:
modules = np.argsort(mod_names)
cons_shape = {}
# extracting constant shape.
for qm, constant in data.items():
    for cname, cons in constant.items():
        shape = data[qm][cname].shape
        if cname not in cons_shape:
            cons_shape[cname] = shape
    break
constants = {}
prev_const = {}
for cname, sh in cons_shape.items():
    constants[cname]= np.zeros((len(mod_names),) + sh[:])
    prev_const[cname]= np.zeros((len(mod_names),) + sh[:])

for i, mod in enumerate(modules):
    for cname, cval in constants.items():
        cval[i] = data[mod_names[mod]][cname]
        prev_const[cname][i] = old_cons[mod_names[mod]][cname]
mod_names = np.array(mod_names)[modules]

In [ ]:
display(Markdown('## Processed modules ##'))

fig, ax = plt.subplots(1, figsize=(10, 10))
ax.set_axis_off()

ax.set_xlim(0, 90)
ax.set_ylim(0, 75)
asic_pos = 5

q_st = 8

l_y = 6
l_x = 5
counter = 0

for iq, q_x in enumerate([[43,66],[45,34],[4,32],[2,64]]):
    for im in range(4):
        color = 'gray'
        if 'Q{}M{}'.format(iq+1, im+1) in mod_names:
            color = 'green'
        if 'Noise' not in constants.keys() or \
            np.nanmean(constants['Noise'][counter, :, :, :, 0]) == 0:
            color = 'red'
        if counter < len(mod_names)-1:
            counter += 1
        x = q_x[0]
        for i_as in range(8):
            ax.add_patch(matplotlib.patches.Rectangle((x,q_x[1]-q_st*im), l_x, l_y, linewidth=2,edgecolor='darkgreen',
                                           facecolor=color, fill=True))
            x += asic_pos
        ax.text(q_x[0]+14.5, q_x[1]-q_st*im+1.5, 'Q{}M{}'.format(
            iq+1, im+1),  fontsize=24, color='gold')

_ = ax.legend(handles=[patches.Patch(facecolor='red', label='No data'),
                       patches.Patch(facecolor='gray', label='Not processed'),
                       patches.Patch(facecolor='green', label='Processed')],
              loc='outside-top', ncol=3, bbox_to_anchor=(0.1, 0.25, 0.7, 0.8))

## Summary figures across Modules ##

The following plots give an overview of calibration constants averaged across pixels and memory cells. A bad pixel mask is applied.

In [ ]:
#Initializing AGIPD geometry
geom = AGIPD_1MGeometry.from_quad_positions(quad_pos=[
        (-525, 625),
        (-550, -10),
        (520, -160),
        (542.5, 475),
    ])


Mod_data=OrderedDict()
for const_name, const in constants.items():

    Mod_data[const_name] = OrderedDict()
    Mod_data['d-{}'.format(const_name)] = OrderedDict()
    Mod_data['dpct-{}'.format(const_name)] = OrderedDict()
    display(Markdown('##### {}'.format(const_name)))

    for gain in range(3):

        # Avoid plotting for high gain offset in 3 index 
        # for Threshold gain dimension.
        if const_name == 'ThresholdsDark':
            if gain == 2:
                continue
            glabel = threshold_names
        else:
            glabel = gain_names

        for i in range(16):
            qm = "Q{}M{}".format(i//4 + 1, i % 4 + 1)
            if const.shape[0] > i:
                values = np.nanmean(const[i, :, :, :, gain], axis=2)
                dval = np.nanmean(prev_const[const_name][i, :, :, :, gain], axis=2)


                values[values == 0] = np.nan
                dval[dval == 0] = np.nan
                dval = values - dval

                dval_pct = dval/values * 100

                values = np.moveaxis(values, 0, -1).reshape(1, values.shape[1], values.shape[0])
                dval = np.moveaxis(dval, 0, -1).reshape(1, dval.shape[1], dval.shape[0])
                dval_pct = np.moveaxis(dval_pct, 0, -1).reshape(1, dval_pct.shape[1], dval_pct.shape[0])
            else:
                # if module not available fill arrays with nan
                values = np.zeros((1, 512, 128),dtype=np.float64)
                values[values == 0] = np.nan
                dval = values 
                dval_pct = dval
            try:
                Mod_data[const_name][gain_names[gain]] = np.concatenate((Mod_data[const_name][gain_names[gain]],
                                                                         values), axis=0)
                Mod_data['d-{}'.format(const_name)][gain_names[gain]] = \
                            np.concatenate((Mod_data['d-{}'.format(const_name)][gain_names[gain]],
                                                                         dval), axis=0)
                Mod_data['dpct-{}'.format(const_name)][gain_names[gain]] = \
                            np.concatenate((Mod_data['dpct-{}'.format(const_name)][gain_names[gain]],
                                                                         dval_pct), axis=0)
            except:
                Mod_data[const_name][gain_names[gain]] = values
                Mod_data['d-{}'.format(const_name)][gain_names[gain]] = dval
                Mod_data['dpct-{}'.format(const_name)][gain_names[gain]] = dval_pct

        vmin, vmax = get_range(Mod_data[const_name][gain_names[gain]], 2)
        dvmin, dvmax = get_range(Mod_data['d-{}'.format(const_name)][gain_names[gain]], 2)
        dpctvmin, dpctvmax = get_range(Mod_data['dpct-{}'.format(const_name)][gain_names[gain]], 2)
        # Plotting constant overall modules.
        display(Markdown('###### {} ######'.format(glabel[gain])))
        
        gs = gridspec.GridSpec(2, 2)
        fig = plt.figure(figsize=(24, 32))
        
        ax0 = fig.add_subplot(gs[0, :])
        ax1 = fig.add_subplot(gs[1, 0])
        ax2 = fig.add_subplot(gs[1, 1])
        geom.plot_data_fast(Mod_data[const_name][gain_names[gain]], vmin=vmin, vmax=vmax,
                             ax=ax0, colorbar={
                            'shrink': 0.9,
                            'pad': 0.05})

        colorbar = ax0.images[0].colorbar
        if const_name != 'BadPixelsDark':
            colorbar.set_label('ADUs')

        ax0.set_title('{} {}'.format(const_name, glabel[gain]), fontsize=15)
        ax0.set_xlabel('Columns', fontsize=15)
        ax0.set_ylabel('Rows', fontsize=15)

        # Plotting the difference with previous constants in ADUs and %
        geom.plot_data_fast(Mod_data['d-{}'.format(const_name)][gain_names[gain]],
                            vmin=dvmin, vmax=dvmax, ax=ax1,colorbar={
                            'shrink': 0.6,
                            'pad': 0.1,
                            'orientation': 'horizontal'})
        colorbar = ax1.images[0].colorbar
        if const_name != 'BadPixelsDark':
            colorbar.set_label('ADUs')
        geom.plot_data_fast(Mod_data['dpct-{}'.format(const_name)][gain_names[gain]], 
                            vmin=dpctvmin, vmax=dpctvmax, ax=ax2,colorbar={
                            'shrink': 0.6,
                            'pad': 0.1,
                            'orientation': 'horizontal'})
        colorbar = ax2.images[0].colorbar
        colorbar.set_label('%')
        ax1.set_title('Difference with previous {} {}'.format(const_name, 
                                                                   glabel[gain]), fontsize=15)
        ax1.set_xlabel('Columns', fontsize=15)
        ax1.set_ylabel('Rows', fontsize=15)
        ax2.set_title('Difference with previous {} {} (%)'.format(const_name, glabel[gain]), fontsize=15)
        ax2.set_xlabel('Columns', fontsize=15)
        ax2.set_ylabel('Rows', fontsize=15)
        plt.show()
        

In [ ]:
# Loop over capacitor settings, modules, constants
for const_name, const in constants.items():

    display(Markdown('### Summary across Modules - {}'.format(const_name)))
    for gain in range(3):

        if const_name == 'ThresholdsDark':
            if gain == 2:
                continue
            glabel = threshold_names
        else:
            glabel = gain_names
            
        data = np.copy(const[:, :, :, :, gain])
        if const_name != 'BadPixelsDark':
            label = '{} value [ADU], good pixels only'.format(const_name)
            data[constants['BadPixelsDark'][:, :, :, :, gain] > 0] = np.nan
            datamean = np.nanmean(data, axis=(1, 2))

            fig = plt.figure(figsize=(15, 6), tight_layout={
                             'pad': 0.2, 'w_pad': 1.3, 'h_pad': 1.3})
            ax = fig.add_subplot(121)
        else:
            label = 'Fraction of bad pixels'
            data[data > 0] = 1.0
            datamean = np.nanmean(data, axis=(1, 2))
            datamean[datamean == 1.0] = np.nan

            fig = plt.figure(figsize=(15, 6), tight_layout={
                             'pad': 0.2, 'w_pad': 1.3, 'h_pad': 1.3})
            ax = fig.add_subplot(111)

        d = []
        for im, mod in enumerate(datamean):
            d.append({'x': np.arange(mod.shape[0]),
                      'y': mod,
                      'drawstyle': 'steps-pre',
                      'label': mod_names[im],
                      })

        _ = simplePlot(d, figsize=(10, 10), xrange=(-12, 510),
                            x_label='Memory Cell ID',
                            y_label=label,
                            use_axis=ax,
                            title='{}'.format(glabel[gain]),
                            title_position=[0.5, 1.18],
                            legend='outside-top-ncol6-frame', legend_size='18%',
                            legend_pad=0.00)

        if const_name != 'BadPixelsDark':
            ax = fig.add_subplot(122)
            label = '## $\sigma$ {} [ADU], good pixels only'.format(const_name)
            d = []
            for im, mod in enumerate(np.nanstd(data, axis=(1, 2))):
                d.append({'x': np.arange(mod.shape[0]),
                          'y': mod,
                          'drawstyle': 'steps-pre',
                          'label': mod_names[im],
                          })

            _ = simplePlot(d, figsize=(10, 10), xrange=(-12, 510),
                                x_label='Memory Cell ID',
                                y_label=label,
                                use_axis=ax,
                                title='{} $\sigma$'.format(glabel[gain]),
                                title_position=[0.5, 1.18],
                                legend='outside-top-ncol6-frame', legend_size='18%',
                                legend_pad=0.00)

        plt.show()

## Summary tables across Modules ##

Tables show values averaged across all pixels and memory cells of a given detector module.

In [ ]:
if u'$' in tabulate.LATEX_ESCAPE_RULES:
    del(tabulate.LATEX_ESCAPE_RULES[u'$'])
    
if u'\\' in tabulate.LATEX_ESCAPE_RULES:
    del(tabulate.LATEX_ESCAPE_RULES[u'\\'])

In [ ]:
head = ['Module', 'High gain', 'Medium gain', 'Low gain']
head_th = ['Module', 'High threshold', 'Medium threshold']
for const_name, const in constants.items():
    table = []

    for i_mod, mod in enumerate(mod_names):

        t_line = [mod]
        for gain in range(3):
            
            if const_name == 'ThresholdsDark': 
                if gain == 2:
                    continue
                header = head_th
            else:
                header = head

            data = np.copy(const[i_mod, :, :, :, gain])
            if const_name == 'BadPixelsDark':
                data[data > 0] = 1.0
                datasum = np.nansum(data)
                datamean = np.nanmean(data)
                if datamean == 1.0:
                    datamean = np.nan
                    datasum = np.nan

                t_line.append('{:6.0f} ({:6.3f}) '.format(
                    datasum, datamean))

                label = '### Number (fraction) of bad pixels ###'
            else:

                data[constants['BadPixelsDark']
                     [i_mod, :, :, :, gain] > 0] = np.nan

                t_line.append('{:6.1f} $\\pm$ {:6.1f}'.format(
                    np.nanmean(data), np.nanstd(data)))
                label = '### Average {} [ADU], good pixels only ###'.format(const_name)

        table.append(t_line)

    display(Markdown(label))
    md = display(Latex(tabulate.tabulate(
        table, tablefmt='latex', headers=header)))